In [1]:
from datasets import load_dataset, DatasetDict
import os

dataset = load_dataset("json", data_files="diversevul_20230702.json")

train_valid = dataset["train"].train_test_split(test_size=0.2, seed=0, train_indices_cache_file_name="train.indices")
train_data, valid_data = train_valid["train"], train_valid["test"]
valid_test = valid_data.train_test_split(test_size=0.5, seed=0, train_indices_cache_file_name="valid.indices", test_indices_cache_file_name="test.indices")
valid_data, test_data = valid_test["train"], valid_test["test"]
dataset = DatasetDict({
    "train": train_data,
    "validation": valid_data,
    "test": test_data,
})

dataset["train"]

Dataset({
    features: ['func', 'target', 'cwe', 'project', 'commit_id', 'hash', 'size', 'message'],
    num_rows: 264393
})

In [2]:
import pandas as pd
df_train = pd.DataFrame(dataset["train"])
#lst_train = pd.DataFrame(dataset["train"]).loc[(dataset['train']['target'] == [1])]['func']
lst_train = df_train.loc[(df_train['target'] == 1)]
lst_train_func = lst_train['func']

In [3]:
lst_train_func = list(lst_train_func)
lst_train_func[1]

'zzip_mem_disk_load(ZZIP_MEM_DISK* dir, ZZIP_DISK* disk)\n{\n    if (dir->list) zzip_mem_disk_unload(dir);\n    ___ struct zzip_disk_entry* entry = zzip_disk_findfirst(disk);\n    for (; entry ; entry = zzip_disk_findnext(disk, entry)) {\n\tZZIP_MEM_DISK_ENTRY* item = zzip_mem_disk_entry_new(disk, entry);\n\tif (dir->last) { dir->last->zz_next = item; }\n\telse { dir->list = item; }; dir->last = item;\n    } ____;\n    dir->disk = disk;\n    return 0;\n}'

In [4]:
lst_train_func_new_zet = []
lst_train_func_new_unzet = []
lst_train_func_new = []
i = 0
while i <= 200:
        lst_train_func_new_zet.append(list(lst_train_func)[i])
        lst_train_func_new_zet.append('\n<sep>\n')
        i += 1


In [5]:
with open("ex_rag_vuln_223.txt", "a") as file:
    file.writelines(lst_train_func_new_zet)

In [6]:
lst_train_func_new_zet[27]

'\n<sep>\n'

In [7]:
import pickle 
from pickle import dump

def load_doc(filename):
    file = open(filename, mode = 'rt', encoding = 'latin-1')
    text = file.read()
    file.close()
    return text

In [8]:
def to_sentences(doc):
    return doc.strip().split('\n<sep>\n')
def sentence_lenghts(sentences):
    lenghts = [len(s.split()) for s in sentences]
    return min(lenghts), max(lenghts)

In [9]:
import re
import string 
import unicodedata
def clean_lines(lines):
    cleaned = list()
    
    for line in lines:
        line = unicodedata.normalize('NFD', line).encode('ascii', 'ignore')
        line = line.decode('latin-1')
        line = line.split()
        line = [word.lower() for word in line]
        cleaned.append(' '.join(line))
    return cleaned 
        

In [11]:
filename = 'ex_rag_vuln_223.pdf'
doc = load_doc(filename)
sentences = to_sentences(doc)
for i in range(len(lst_train_func_new_zet)):
    if i%2 == 0:
        sentences.append(lst_train_func_new_zet[i])
minlen, maxlen = sentence_lenghts(sentences)
print('RAG...: sentences=%d, min=%d, max=%d' % (len(sentences), minlen, maxlen))
cleanf = clean_lines(sentences)
filename = 'ex_rag_vuln_223.pkl'
outfile = open(filename, 'wb')
pickle.dump(cleanf, outfile)
outfile.close()
print(filename, 'saved')


RAG...: sentences=202, min=7, max=158009
ex_rag_vuln_223.pkl saved


In [12]:
from pickle import load
from pickle import dump
from collections import Counter 
def load_clean_sentences(filename):
    return load(open(filename, 'rb'))
def save_clean_sentences(sentences, filename):
    dump(sentences, open(filename, 'wb'))
    print('Saved: %s'%filename)
    

In [19]:
def to_vocab(lines):
    vocab = Counter()
    for line in lines:
        tokens = get_tokens(line)
        vocab.update(tokens)
    return vocab
def trim_vocab(vocab, min_occurrence):
    tokens = [k for k,c in vocab.items() if c >= 2]
    return set(tokens)
def update_dataset(lines, vocab):
    new_lines = list()
    for line in lines:
        new_tokens = list()
        for token in line.split():
            if token in vocab:
                new_tokens.append(token)
            else:
                new_tokens.append('unk')
        new_line = ' '.join(new_tokens)
        new_lines.append(new_line)
    return new_lines


In [20]:
def get_tokens(data):
    data = data.replace('\r', '')
    data = data.replace('\t', ' ')
    data = data.lower()
    
    misc  = [
#        re.compile(r'(//([^\n])+)'),
 #       re.compile(r'((\/\/.*)|(\/\*[\s\S]*?\*\/))'),
  #      re.compile(r'(\s*#[<>.\w\W\d]+)')
    ]
   # for rc in misc:
    #    data = rc.sub('', data)


    
    re_fun = re.compile(r'([_.->\w]+)\s*\([^)]*\)')
    re_var = re.compile(r'\s*([_\d\w]*)(\s*)=(\s*)[^;]*')

    var_idx = 0 
    func_idx = 0
    words = []
    for line in data.split('\n'):

        s = re_var.search(line)
        if s:
            var_idx += 1
            var_name = s.group(1)
            line = re.compile(r'([_\d\w]+\s*=\s*)').sub('var%d = '% var_idx, line)

        s = re_fun.search(line)
        if s:
            got_stmt = False
            for st in ['if','for','while']:
                if line.find(st) >=0:
                    got_stmt = True
                    break
            if not got_stmt:
                func_idx += 1
                func = s.group(1)
                line = line.replace('%s' % func, 'func%d' % func_idx)

        chars = ['(', ')', '{', '}', '*', '/', '+', '-', '=', ';', ',']
        for ch in chars:
            line = line.replace(ch, ' %s ' % ch)

        if line and len(line) >= 1:         
            for w in line.split(' '):
                w = w.strip()
                if w:
                    words.append(w) 

    return words




In [206]:
import fitz 
from tqdm.auto import tqdm  

def text_formatter(text: str) -> str:
    
    cleaned_text = text.replace("\n", " ").strip() 
    
    return cleaned_text


In [208]:
def open_and_read_pdf_2(pdf_path: str) -> list[dict]: #!!!
    with open('ex_rag_vuln_223.txt', 'r') as file:
        docs = file.read()
    dc= docs.split('<sep>')
    doc = fitz.open('ex_rag_vuln_223.pdf') 
    p_and_t = []
    a = 0
    i = 0
    for page_number, page in tqdm(enumerate(doc)): 
        while i <=402:
            text = page.get_text()  
            text = text_formatter(text)
            p_and_t.append({"page_number": page_number,  
                                "page_char_count": len(text),
                                "page_word_count": len(text.split(" ")),
                                "page_sentence_count_raw": len(text.split("<sep>")),
                                "page_token_count": len(text) / 4,
                                 "text": dc[i]})
            i += 1 
    return p_and_t
pages_and_texts_2 = open_and_read_pdf_2(pdf_path='ex_rag_vuln_223.pdf')

0it [00:00, ?it/s]

In [209]:
print(pages_and_texts_2[0])

{'page_number': 0, 'page_char_count': 983, 'page_word_count': 325, 'page_sentence_count_raw': 1, 'page_token_count': 245.75, 'text': 'static boolean ReadICCProfile(j_decompress_ptr jpeg_info)\n{\n  char\n    magick[12];\n\n  ErrorManager\n    *error_manager;\n\n  ExceptionInfo\n    *exception;\n\n  Image\n    *image;\n\n  MagickBooleanType\n    status;\n\n  register ssize_t\n    i;\n\n  register unsigned char\n    *p;\n\n  size_t\n    length;\n\n  StringInfo\n    *icc_profile,\n    *profile;\n\n  /*\n    Read color profile.\n  */\n  length=(size_t) ((size_t) GetCharacter(jpeg_info) << 8);\n  length+=(size_t) GetCharacter(jpeg_info);\n  length-=2;\n  if (length <= 14)\n    {\n      while (length-- > 0)\n        if (GetCharacter(jpeg_info) == EOF)\n          break;\n      return(TRUE);\n    }\n  for (i=0; i < 12; i++)\n    magick[i]=(char) GetCharacter(jpeg_info);\n  if (LocaleCompare(magick,ICC_PROFILE) != 0)\n    {\n      /*\n        Not a ICC profile, return.\n      */\n      for (i=0

In [210]:
filename = 'ex_rag_vuln_223.pkl'
lines1 = load_clean_sentences(filename)
vocab = to_vocab(lines1)
print('rag Vocabulary: %d' % len(vocab))
vocab = trim_vocab(vocab, 5)
print('New rag Vocabulary: %d' % len(vocab))
#lines1 = update_dataset(lines1, vocab)
filename = 'rag_vocab_vuln_223.pkl'
save_clean_sentences(lines1, filename)
print(len(lines1))
for i in range(34,70): #example
    print("line",i,":",lines1[i])

rag Vocabulary: 120831
New rag Vocabulary: 9631
Saved: rag_vocab_vuln_223.pkl
202
line 34 : getsize_gnutar( dle_t *dle, int level, time_t dumpsince, char **errmsg) { int pipefd = -1, nullfd = -1; pid_t dumppid; off_t size = (off_t)-1; file *dumpout = null; char *incrname = null; char *basename = null; char *dirname = null; char *inputname = null; file *in = null; file *out = null; char *line = null; char *cmd = null; char *command = null; char dumptimestr[80]; struct tm *gmtm; int nb_exclude = 0; int nb_include = 0; gptrarray *argv_ptr = g_ptr_array_new(); char *file_exclude = null; char *file_include = null; times_t start_time; int infd, outfd; ssize_t nb; char buf[32768]; char *qdisk = quote_string(dle->disk); char *gnutar_list_dir; amwait_t wait_status; char tmppath[path_max]; if (level > 9) return -2; /* planner will not even consider this level */ if(dle->exclude_file) nb_exclude += dle->exclude_file->nb_element; if(dle->exclude_list) nb_exclude += dle->exclude_list->nb_element; i

In [211]:
import pandas as pd
df = pd.DataFrame(pages_and_texts_2)
df

page_number  page_char_count  page_word_count  page_sentence_count_raw   
0              0              983              325                        1  \
1              0              983              325                        1   
2              0              983              325                        1   
3              0              983              325                        1   
4              0              983              325                        1   
..           ...              ...              ...                      ...   
398            0              983              325                        1   
399            0              983              325                        1   
400            0              983              325                        1   
401            0              983              325                        1   
402            0              983              325                        1   

     page_token_count                                               text  
0              245.75  static boolean ReadICCProfile(j_decompress_ptr...  
1              245.75  \nzzip_mem_disk_load(ZZIP_MEM_DISK* dir, ZZIP_...  
2              245.75  \nint rsa_pkcs1_decrypt( rsa_context *ctx,\n  ...  
3              245.75  \nstatic int ehci_process_itd(EHCIState *ehci,...  
4              245.75  \nGF_Filter *gf_fs_load_filter(GF_FilterSessio...  
..                ...                                                ...  
398            245.75  \narch_get_unmapped_area(struct file *filp, un...  
399            245.75  \nofputil_pull_ofp15_group_mod(struct ofpbuf *...  
400            245.75  \nmkstemp_helper (struct obstack *obs, const c...  
401            245.75  \nMagickPrivate ResizeFilter *AcquireResizeFil...  
402            245.75                                                 \n  

[403 rows x 6 columns]

In [212]:
import sys
a = 0
for item in tqdm(pages_and_texts_2):
    item["sentences"] = str(item["text"])
    
    item["page_sentence_count_spacy"] = len(item["sentences"])
    


  0%|          | 0/403 [00:00<?, ?it/s]

In [213]:
import random
random.sample(pages_and_texts_2, k=1)

[{'page_number': 0,
  'page_char_count': 983,
  'page_word_count': 325,
  'page_sentence_count_raw': 1,
  'page_token_count': 245.75,
  'text': '\nint ssh_scp_leave_directory(ssh_scp scp)\n{\n    char buffer[] = "E\\n";\n    int rc;\n    uint8_t code;\n\n    if (scp == NULL) {\n        return SSH_ERROR;\n    }\n\n    if (scp->state != SSH_SCP_WRITE_INITED) {\n        ssh_set_error(scp->session, SSH_FATAL,\n                      "ssh_scp_leave_directory called under invalid state");\n        return SSH_ERROR;\n    }\n\n    rc = ssh_channel_write(scp->channel, buffer, strlen(buffer));\n    if (rc == SSH_ERROR) {\n        scp->state = SSH_SCP_ERROR;\n        return SSH_ERROR;\n    }\n\n    rc = ssh_channel_read(scp->channel, &code, 1, 0);\n    if (rc <= 0) {\n        ssh_set_error(scp->session, SSH_FATAL, "Error reading status code: %s",\n                      ssh_get_error(scp->session));\n        scp->state = SSH_SCP_ERROR;\n        return SSH_ERROR;\n    }\n\n    if (code != 0) {\n    

In [214]:
df = pd.DataFrame(pages_and_texts_2)
df.describe().round(2)

page_number  page_char_count  page_word_count  page_sentence_count_raw   
count        403.0            403.0            403.0                    403.0  \
mean           0.0            983.0            325.0                      1.0   
std            0.0              0.0              0.0                      0.0   
min            0.0            983.0            325.0                      1.0   
25%            0.0            983.0            325.0                      1.0   
50%            0.0            983.0            325.0                      1.0   
75%            0.0            983.0            325.0                      1.0   
max            0.0            983.0            325.0                      1.0   

       page_token_count  page_sentence_count_spacy  
count            403.00                     403.00  
mean             245.75                    3534.55  
std                0.00                    6029.53  
min              245.75                       1.00  
25%              245.75                     652.00  
50%              245.75                    1724.00  
75%              245.75                    3451.00  
max              245.75                   40618.00

In [215]:
pages_and_texts_2

[{'page_number': 0,
  'page_char_count': 983,
  'page_word_count': 325,
  'page_sentence_count_raw': 1,
  'page_token_count': 245.75,
  'text': 'static boolean ReadICCProfile(j_decompress_ptr jpeg_info)\n{\n  char\n    magick[12];\n\n  ErrorManager\n    *error_manager;\n\n  ExceptionInfo\n    *exception;\n\n  Image\n    *image;\n\n  MagickBooleanType\n    status;\n\n  register ssize_t\n    i;\n\n  register unsigned char\n    *p;\n\n  size_t\n    length;\n\n  StringInfo\n    *icc_profile,\n    *profile;\n\n  /*\n    Read color profile.\n  */\n  length=(size_t) ((size_t) GetCharacter(jpeg_info) << 8);\n  length+=(size_t) GetCharacter(jpeg_info);\n  length-=2;\n  if (length <= 14)\n    {\n      while (length-- > 0)\n        if (GetCharacter(jpeg_info) == EOF)\n          break;\n      return(TRUE);\n    }\n  for (i=0; i < 12; i++)\n    magick[i]=(char) GetCharacter(jpeg_info);\n  if (LocaleCompare(magick,ICC_PROFILE) != 0)\n    {\n      /*\n        Not a ICC profile, return.\n      */\n   

In [242]:
num_sentence_chunk_size = 100000000 #random number +-

def split_list(input_list: list, 
               slice_size: int) -> list[list[str]]:
    
    return [input_list[i:i + slice_size] for i in range(0, len(input_list), slice_size)]

for item in tqdm(pages_and_texts_2):
    item["sentence_chunks"] = split_list(input_list=item["sentences"],
                                         slice_size=num_sentence_chunk_size)
    
    item["num_chunks"] = len(item["sentence_chunks"])

  0%|          | 0/403 [00:00<?, ?it/s]

In [ ]:
df = pd.DataFrame(pages_and_texts_2)

In [244]:
import re

pages_and_chunks_2 = []

for item in tqdm(pages_and_texts_2):
    for sentence_chunk in item["sentence_chunks"]:
        chunk_dict = {}
        chunk_dict["page_number"] = item["page_number"]
        
        joined_sentence_chunk = "".join(sentence_chunk).replace("  ", " ").strip()
        joined_sentence_chunk = re.sub(r'\.([A-Z])', r'. \1', joined_sentence_chunk) # ".A" -> ". A" for any full-stop/capital letter combo 
        chunk_dict["sentence_chunk"] = joined_sentence_chunk

        chunk_dict["chunk_char_count"] = len(joined_sentence_chunk)
        chunk_dict["chunk_word_count"] = len([word for word in joined_sentence_chunk.split(" ")])
        chunk_dict["chunk_token_count"] = len(joined_sentence_chunk) / 4 # 1 token = ~4 characters
        
        pages_and_chunks_2.append(chunk_dict)


len(pages_and_chunks_2)

  0%|          | 0/403 [00:00<?, ?it/s]

403

In [245]:
pages_and_chunks_2

[{'page_number': 0,
  'sentence_chunk': 'static boolean ReadICCProfile(j_decompress_ptr jpeg_info)\n{\n char\n  magick[12];\n\n ErrorManager\n  *error_manager;\n\n ExceptionInfo\n  *exception;\n\n Image\n  *image;\n\n MagickBooleanType\n  status;\n\n register ssize_t\n  i;\n\n register unsigned char\n  *p;\n\n size_t\n  length;\n\n StringInfo\n  *icc_profile,\n  *profile;\n\n /*\n  Read color profile.\n */\n length=(size_t) ((size_t) GetCharacter(jpeg_info) << 8);\n length+=(size_t) GetCharacter(jpeg_info);\n length-=2;\n if (length <= 14)\n  {\n   while (length-- > 0)\n    if (GetCharacter(jpeg_info) == EOF)\n     break;\n   return(TRUE);\n  }\n for (i=0; i < 12; i++)\n  magick[i]=(char) GetCharacter(jpeg_info);\n if (LocaleCompare(magick,ICC_PROFILE) != 0)\n  {\n   /*\n    Not a ICC profile, return.\n   */\n   for (i=0; i < (ssize_t) (length-12); i++)\n    if (GetCharacter(jpeg_info) == EOF)\n     break;\n   return(TRUE);\n  }\n (void) GetCharacter(jpeg_info); /* id */\n (void) GetCh

In [246]:
df = pd.DataFrame(pages_and_chunks_2)
df.describe().round(2)

page_number  chunk_char_count  chunk_word_count  chunk_token_count
count        403.0            403.00            403.00             403.00
mean           0.0           3236.76            519.90             809.19
std            0.0           5315.79           1014.07            1328.95
min            0.0              0.00              1.00               0.00
25%            0.0            609.00             65.50             152.25
50%            0.0           1606.00            170.00             401.50
75%            0.0           3251.00            455.00             812.75
max            0.0          35013.00           6563.00            8753.25

In [247]:
df

page_number                                     sentence_chunk   
0              0  static boolean ReadICCProfile(j_decompress_ptr...  \
1              0  zzip_mem_disk_load(ZZIP_MEM_DISK* dir, ZZIP_DI...   
2              0  int rsa_pkcs1_decrypt( rsa_context *ctx,\n    ...   
3              0  static int ehci_process_itd(EHCIState *ehci,\n...   
4              0  GF_Filter *gf_fs_load_filter(GF_FilterSession ...   
..           ...                                                ...   
398            0  arch_get_unmapped_area(struct file *filp, unsi...   
399            0  ofputil_pull_ofp15_group_mod(struct ofpbuf *ms...   
400            0  mkstemp_helper (struct obstack *obs, const cha...   
401            0  MagickPrivate ResizeFilter *AcquireResizeFilte...   
402            0                                                      

     chunk_char_count  chunk_word_count  chunk_token_count  
0                2447               309             611.75  
1                 431                53             107.75  
2                 607               166             151.75  
3                3549               917             887.25  
4                2873               229             718.25  
..                ...               ...                ...  
398               808                78             202.00  
399              1590               304             397.50  
400               598               112             149.50  
401             20504              3368            5126.00  
402                 0                 1               0.00  

[403 rows x 5 columns]

In [252]:
pages_and_chunks_2

[{'page_number': 0,
  'sentence_chunk': 'static boolean ReadICCProfile(j_decompress_ptr jpeg_info)\n{\n char\n  magick[12];\n\n ErrorManager\n  *error_manager;\n\n ExceptionInfo\n  *exception;\n\n Image\n  *image;\n\n MagickBooleanType\n  status;\n\n register ssize_t\n  i;\n\n register unsigned char\n  *p;\n\n size_t\n  length;\n\n StringInfo\n  *icc_profile,\n  *profile;\n\n /*\n  Read color profile.\n */\n length=(size_t) ((size_t) GetCharacter(jpeg_info) << 8);\n length+=(size_t) GetCharacter(jpeg_info);\n length-=2;\n if (length <= 14)\n  {\n   while (length-- > 0)\n    if (GetCharacter(jpeg_info) == EOF)\n     break;\n   return(TRUE);\n  }\n for (i=0; i < 12; i++)\n  magick[i]=(char) GetCharacter(jpeg_info);\n if (LocaleCompare(magick,ICC_PROFILE) != 0)\n  {\n   /*\n    Not a ICC profile, return.\n   */\n   for (i=0; i < (ssize_t) (length-12); i++)\n    if (GetCharacter(jpeg_info) == EOF)\n     break;\n   return(TRUE);\n  }\n (void) GetCharacter(jpeg_info); /* id */\n (void) GetCh

In [269]:
#from sentence_transformers import SentenceTransformer
#embedding_model = SentenceTransformer(model_name_or_path="all-mpnet-base-v2", 
#                                      device="cuda") 


In [255]:
embedding_model.to("cuda") 
from sentence_transformers import SentenceTransformer
embedding_model = SentenceTransformer(model_name_or_path="all-mpnet-base-v2", 
                                      device="cuda") 

for item in tqdm(pages_and_chunks_2):
    item["embedding"] = embedding_model.encode(item["sentence_chunk"])

  0%|          | 0/403 [00:00<?, ?it/s]

In [256]:
item["sentence_chunk"]

''

In [258]:
text_chunks_2 = [item["sentence_chunk"] for item in pages_and_chunks_2]

In [259]:
text_chunk_embeddings_2 = embedding_model.encode(text_chunks_2,
                                               batch_size=32, 
                                               convert_to_tensor=True) 

text_chunk_embeddings_2

tensor([[ 0.0200, -0.0177, -0.0158,  ...,  0.0268,  0.0058, -0.0136],
        [ 0.0054, -0.0582,  0.0079,  ..., -0.0469, -0.0119, -0.0182],
        [ 0.0038, -0.0047,  0.0038,  ...,  0.0115, -0.0046, -0.0575],
        ...,
        [ 0.0355, -0.0524, -0.0195,  ...,  0.0233,  0.0408, -0.0163],
        [-0.0532,  0.0074, -0.0043,  ...,  0.0002, -0.0252, -0.0169],
        [-0.0125,  0.0614, -0.0067,  ..., -0.0019, -0.0504, -0.0190]],
       device='cuda:0')

In [261]:
#save 
text_chunks_and_embeddings_df = pd.DataFrame(pages_and_chunks_2)
embeddings_df_save_path = "rag_chunks_and_vuln_df_2.csv"
text_chunks_and_embeddings_df.to_csv(embeddings_df_save_path, index=False)

In [262]:
text_chunks_and_embedding_df_load = pd.read_csv(embeddings_df_save_path)
text_chunks_and_embedding_df_load.head()

page_number                                     sentence_chunk   
0            0  static boolean ReadICCProfile(j_decompress_ptr...  \
1            0  zzip_mem_disk_load(ZZIP_MEM_DISK* dir, ZZIP_DI...   
2            0  int rsa_pkcs1_decrypt( rsa_context *ctx,\n    ...   
3            0  static int ehci_process_itd(EHCIState *ehci,\n...   
4            0  GF_Filter *gf_fs_load_filter(GF_FilterSession ...   

   chunk_char_count  chunk_word_count  chunk_token_count   
0              2447               309             611.75  \
1               431                53             107.75   
2               607               166             151.75   
3              3549               917             887.25   
4              2873               229             718.25   

                                           embedding  
0  [ 1.99929141e-02 -1.77262314e-02 -1.58334374e-...  
1  [ 5.42101916e-03 -5.82121387e-02  7.90116843e-...  
2  [ 3.84714990e-03 -4.65673115e-03  3.84586491e-...  
3  [ 8.10697023e-03 -6.40672967e-02 -4.24665287e-...  
4  [ 2.98015177e-02 -1.34511525e-03  2.77123926e-...

In [263]:
import random

import torch
import numpy as np 
import pandas as pd

device = "cuda" if torch.cuda.is_available() else "cpu"

text_chunks_and_embedding_df = pd.read_csv("rag_chunks_and_vuln_df_2.csv")

text_chunks_and_embedding_df["embedding"] = text_chunks_and_embedding_df["embedding"].apply(lambda x: np.fromstring(x.strip("[]"), sep=" "))

pages_and_chunks = text_chunks_and_embedding_df.to_dict(orient="records")

embeddings = torch.tensor(np.array(text_chunks_and_embedding_df["embedding"].tolist()), dtype=torch.float32).to(device)
embeddings.shape

torch.Size([403, 768])

In [264]:
from sentence_transformers import util, SentenceTransformer

embedding_model = SentenceTransformer(model_name_or_path="all-mpnet-base-v2", 
                                      device=device) 

/home/lera/.local/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [265]:
import textwrap

def print_wrapped(text, wrap_length=200):
    wrapped_text = textwrap.fill(text, wrap_length)
    print(wrapped_text)
import torch

def dot_product(vector1, vector2):
    return torch.dot(vector1, vector2)

def cosine_similarity(vector1, vector2):
    dot_product = torch.dot(vector1, vector2)

    norm_vector1 = torch.sqrt(torch.sum(vector1**2))
    norm_vector2 = torch.sqrt(torch.sum(vector2**2))

    return dot_product / (norm_vector1 * norm_vector2)


In [271]:
def relevant_resources(query: str,
                                embeddings: torch.tensor,
                                model: SentenceTransformer=embedding_model,
                                n_resources_to_return: int=5,
                                print_time: bool=True):
    
    query_embedding = model.encode(query, 
                                   convert_to_tensor=True) 
    
    dot_scores = util.dot_score(query_embedding, embeddings)[0]

    scores, indices = torch.topk(input=dot_scores, 
                                 k=n_resources_to_return)

    return scores, indices

def print_top(query: str,
            embeddings: torch.tensor,
            pages_and_chunks: list[dict]=pages_and_chunks,
            n_resources_to_return: int=5):
    
    scores, indices = retrieve_relevant_resources(query=query,
                                                  embeddings=embeddings,
                                                  n_resources_to_return=n_resources_to_return)
    
    print(f"Query: {query}\n")
    
    print("Results:")
    
    for score, index in zip(scores, indices):
        print(f"Score: {score:.4f}")
        
        print_wrapped(pages_and_chunks[index]["sentence_chunk"])
        
        print(f"Page number: {pages_and_chunks[index]['page_number']}")
        
        print("\n")

In [272]:
query = "zzip_mem_disk_load(ZZIP_MEM_DISK* dir, ZZIP_DISK* disk){if (dir->list)\
zzip_mem_disk_unload(dir); ___ struct zzip_disk_entry* entry = zzip_disk_findfirst(disk);\
for (; entry ; entry = zzip_disk_findnext(disk, entry)) {ZZIP_MEM_DISK_ENTRY* item =\
zzip_mem_disk_entry_new(disk, entry);if (dir->last) { dir->last->zz_next = item; }else\
{ dir->list = item; }; dir->last = item; } ____;dir->disk = disk;return 0;}"

scores, indices = relevant_resources(query=query,
                                              embeddings=embeddings)
scores, indices

(tensor([1.0000, 1.0000, 0.7426, 0.7426, 0.4881], device='cuda:0'),
 tensor([  1, 202, 221,  20,  55], device='cuda:0'))

In [273]:
print_top(query=query,embeddings=embeddings)

Query: zzip_mem_disk_load(ZZIP_MEM_DISK* dir, ZZIP_DISK* disk){if (dir->list) zzip_mem_disk_unload(dir); ___ struct zzip_disk_entry* entry = zzip_disk_findfirst(disk); for (; entry ; entry = zzip_disk_findnext(disk, entry)) {ZZIP_MEM_DISK_ENTRY* item = zzip_mem_disk_entry_new(disk, entry);if (dir->last) { dir->last->zz_next = item; }else { dir->list = item; }; dir->last = item; } ____;dir->disk = disk;return 0;}

Results:
Score: 1.0000
zzip_mem_disk_load(ZZIP_MEM_DISK* dir, ZZIP_DISK* disk) {   if (dir->list) zzip_mem_disk_unload(dir);   ___ struct zzip_disk_entry* entry = zzip_disk_findfirst(disk);   for (; entry ; entry =
zzip_disk_findnext(disk, entry)) {         ZZIP_MEM_DISK_ENTRY* item = zzip_mem_disk_entry_new(disk, entry);         if (dir->last) { dir->last->zz_next = item; }         else { dir->list = item; };
dir->last = item;   } ____;   dir->disk = disk;   return 0; }
Page number: 0


Score: 1.0000
zzip_mem_disk_load(ZZIP_MEM_DISK* dir, ZZIP_DISK* disk) {   if (dir->list) z

In [274]:
query2 = 'static void ip6gre_err(struct sk_buff *skb, struct inet6_skb_parm *opt,\
        u8 type, u8 code, int offset, __be32 info)\
{\
    const struct ipv6hdr *ipv6h = (const struct ipv6hdr *)skb->data;\
    __be16 *p = (__be16 *)(skb->data + offset);\
    int grehlen = offset + 4;\
    struct ip6_tnl *t;\
    __be16 flags;\
\
    flags = p[0];\
    if (flags&(GRE_CSUM|GRE_KEY|GRE_SEQ|GRE_ROUTING|GRE_VERSION)) {\
        if (flags&(GRE_VERSION|GRE_ROUTING))\
            return;\
        if (flags&GRE_KEY) {\
            grehlen += 4;\
            if (flags&GRE_CSUM)\
                grehlen += 4;\
        }\
    }'
scores, indices = relevant_resources(query=query2,
                                              embeddings=embeddings)
scores, indices

(tensor([0.7902, 0.7902, 0.7863, 0.7863, 0.7572], device='cuda:0'),
 tensor([120, 321, 378, 177, 168], device='cuda:0'))

In [275]:
print_top(query=query2,embeddings=embeddings)

Query: static void ip6gre_err(struct sk_buff *skb, struct inet6_skb_parm *opt,        u8 type, u8 code, int offset, __be32 info){    const struct ipv6hdr *ipv6h = (const struct ipv6hdr *)skb->data;    __be16 *p = (__be16 *)(skb->data + offset);    int grehlen = offset + 4;    struct ip6_tnl *t;    __be16 flags;    flags = p[0];    if (flags&(GRE_CSUM|GRE_KEY|GRE_SEQ|GRE_ROUTING|GRE_VERSION)) {        if (flags&(GRE_VERSION|GRE_ROUTING))            return;        if (flags&GRE_KEY) {            grehlen += 4;            if (flags&GRE_CSUM)                grehlen += 4;        }    }

Results:
Score: 0.7902
static int rawv6_sendmsg(struct sock *sk, struct msghdr *msg, size_t len) {         struct ipv6_txoptions opt_space;         DECLARE_SOCKADDR(struct sockaddr_in6 *, sin6, msg->msg_name);
struct in6_addr *daddr, *final_p, final;         struct inet_sock *inet = inet_sk(sk);         struct ipv6_pinfo *np = inet6_sk(sk);         struct raw6_sock *rp = raw6_sk(sk);         struct
ipv6_txopt